# Dataset and Env Setup

In [ ]:
%%bash

mkdir -p data/
mkdir -p lme_jsons/
cd data/
wget -c https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_oracle.json
wget -c https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_s_cleaned.json
wget -c https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_m_cleaned.json
cd ..


--2026-01-21 20:35:46--  https://huggingface.co/datasets/xiaowu0162/longmemeval-cleaned/resolve/main/longmemeval_oracle.json
Resolving huggingface.co (huggingface.co)... 3.169.137.5, 3.169.137.19, 3.169.137.119, ...
Connecting to huggingface.co (huggingface.co)|3.169.137.5|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://us.gcp.cdn.hf.co/xet-bridge-us/68cde13e82e1bf61a6602263/7d958f239f452f33a5368e31d0a3dc6ffb4f225036ddd46fc71370a6dc1e2db6?response-content-disposition=inline%3B+filename*%3DUTF-8%27%27longmemeval_oracle.json%3B+filename%3D%22longmemeval_oracle.json%22%3B&response-content-type=application%2Fjson&Expires=1769031346&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiRXBvY2hUaW1lIjoxNzY5MDMxMzQ2fX0sIlJlc291cmNlIjoiaHR0cHM6Ly91cy5nY3AuY2RuLmhmLmNvL3hldC1icmlkZ2UtdXMvNjhjZGUxM2U4MmUxYmY2MWE2NjAyMjYzLzdkOTU4ZjIzOWY0NTJmMzNhNTM2OGUzMWQwYTNkYzZmZmI0ZjIyNTAzNmRkZDQ2ZmM3MTM3MGE2ZGMxZTJkYjZcXD9yZXNwb25zZS1jb250ZW50LWRpc3Bvc2l0aW

In [ ]:
%%capture
!pip install -U transformers datasets bitsandbytes accelerate


In [ ]:
!pip install openai google-generativeai


In [ ]:
import torch
print("cuda available:", torch.cuda.is_available())
!nvidia-smi


cuda available: True
Wed Jan 21 20:47:06 2026       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 550.54.15              Driver Version: 550.54.15      CUDA Version: 12.4     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  Tesla T4                       Off |   00000000:00:04.0 Off |                    0 |
| N/A   42C    P8              9W /   70W |       2MiB /  15360MiB |      0%      Default |
|                                         |                        |                  N/A |
+--------------------------

In [ ]:
import json
from time import sleep
import os
from tqdm import tqdm

flag = 0

# Path to file
json_path = "/content/data/longmemeval_oracle.json"
json_path2 = "/content/data/longmemeval_m_cleaned.json"
json_path3 = "/content/data/longmemeval_s_cleaned.json"

if flag == 0:
  # Load the whole JSON into memory
  with open(json_path, "r", encoding="utf-8") as f:
      LME = json.load(f)
elif flag == 1:
  with open(json_path2, "r", encoding="utf-8") as f:
      LME = json.load(f)
elif flag == 2:
  with open(json_path3, "r", encoding="utf-8") as f:
      LME = json.load(f)


In [ ]:
import json
import torch
import time

# =============================================================================
# MODIFIED: Answer-First Reasoning Verification Approach
# =============================================================================
# Instead of asking the LLM to find the answer, we:
# 1. Give the LLM the correct answer upfront
# 2. Ask it to explain HOW that answer can be derived from the context
# 3. Verify that the reasoning actually supports the answer
# =============================================================================

def build_history_text_answer_sessions(example, max_chars=50000, debug=True):
    """
    Build history text keeping only sessions that contain the answer.
    Prefers example['answer_session_ids']; falls back to per-turn 'has_answer'.

    Also prints how many sessions were removed.
    """
    parts = []

    sess_ids = example["haystack_session_ids"]
    sessions = example["haystack_sessions"]
    total_sessions = len(sess_ids)

    # Prefer explicit list of answer-bearing session ids if available
    answer_sess_ids = set(example.get("answer_session_ids", []))

    kept_sessions = 0
    removed_sessions = 0

    for sess_id, session in zip(sess_ids, sessions):
        # Decide whether to keep this session
        if answer_sess_ids:
            keep = sess_id in answer_sess_ids
        else:
            # Fallback: look for any turn with has_answer == True
            keep = any(turn.get("has_answer") for turn in session)

        if not keep:
            removed_sessions += 1
            continue

        kept_sessions += 1
        parts.append(f"=== Session {sess_id} ===")
        for i, turn in enumerate(session):
            role = turn.get("role", "user")
            role_name = "User" if role == "user" else "Assistant"
            # Added logic 1/15/2026
            if turn['has_answer']:
              parts.append(f"[{role_name} {i}] {turn['content']}")

    # logging
    if debug:
        print(f"[FILTER] kept {kept_sessions} / {total_sessions} sessions "
              f"({removed_sessions} removed).")

    text = "\n".join(parts)

    if debug:
        print(f"[DEBUG] Text length: {len(text)} chars")

    if len(text) > max_chars:
        if debug:
            print(f"[HIT TXT TRUNCATION at {max_chars}]")
        qt = example.get("question_type")
        if qt == "single-session-preference":
            # For preference mining, keep the *beginning*
            text = text[:max_chars]
        else:
            # For other tasks, keep the tail
            text = text[-max_chars:]

    return text


def build_system_prompt_answer_verification(example):
    """
    MODIFIED: Build system prompt for answer verification approach.

    The LLM is given the correct answer and must explain how it can be
    derived from the conversation history.
    """
    qt = example["question_type"]

    # Base prompt for answer verification
    base_prompt = (
        "detailed thinking on\n\n"
        "You are a reasoning verification assistant.\n"
        "You will be given:\n"
        "1. A conversation history between a user and an assistant\n"
        "2. A question about the conversation\n"
        "3. The CORRECT ANSWER to the question\n\n"
        "Your task is to VERIFY that this answer is correct by:\n"
        "1. Finding the specific evidence in the conversation that supports the answer\n"
        "2. Explaining step-by-step how you would derive this answer from the evidence\n"
        "3. Confirming the answer is correct OR flagging if you cannot find supporting evidence\n\n"
    )

    if qt == "temporal-reasoning":
        task_specific = (
            "This is a TEMPORAL REASONING question about the ORDER of events.\n"
            "Focus on:\n"
            "- Finding relative time phrases ('three weeks ago', 'last month', 'yesterday')\n"
            "- The narrative order of events described\n"
            "- Any dates or time references mentioned\n\n"
        )
    elif qt == "single-session-preference":
        task_specific = (
            "This is a PREFERENCE MINING question.\n"
            "Focus on:\n"
            "- What tools/products/topics the user prefers\n"
            "- What level of detail they want\n"
            "- What they seem NOT to want\n\n"
        )
    elif qt == "single-session-answer":
        task_specific = (
            "This is a FACTUAL question about specific information.\n"
            "Focus on:\n"
            "- Finding the exact piece of information requested\n"
            "- Locating which session/turn contains this information\n\n"
        )
    else:
        task_specific = (
            "Find the relevant information in the conversation and explain how it leads to the answer.\n\n"
        )

    response_format = (
        "Return JSON with these keys:\n"
        '- "evidence": Quote or reference the specific text from the conversation that supports the answer\n'
        '- "reasoning": Step-by-step explanation of how the evidence leads to the answer\n'
        '- "verified": true if you found clear evidence supporting the answer, false if the answer seems incorrect or unsupported\n'
        '- "answer": Restate the provided answer (to confirm understanding)\n'
    )

    return base_prompt + task_specific + response_format


def cot_annotate_answer_verification_local(example, ground_truth_answer, max_new_tokens=512, max_prompt_tokens=65536, debug=True):
    """
    MODIFIED: Generate reasoning that verifies a given answer using local model.

    Instead of asking the model to find the answer, we give it the answer
    and ask it to explain how that answer can be derived.
    """
    question = example["question"]
    history_text = build_history_text_answer_sessions(example, max_chars=50000, debug=debug)
    system = build_system_prompt_answer_verification(example)

    # Build chat messages with the answer provided
    messages = [
        {"role": "system", "content": system},
        {
            "role": "user",
            "content": (
                "CONVERSATION HISTORY:\n"
                f"{history_text}\n\n"
                f"QUESTION: {question}\n\n"
                f"CORRECT ANSWER: {ground_truth_answer}\n\n"
                "Your task: Verify this answer is correct by finding evidence and explaining the reasoning.\n"
                "If you cannot find evidence supporting this answer, set 'verified': false.\n\n"
                'Respond ONLY with valid JSON:\n'
                '{"evidence": "...", "reasoning": "...", "verified": true/false, "answer": "..."}\n\n'
                "JSON:"
            ),
        },
    ]

    if debug:
        print(f"[DEBUG] System prompt length: {len(system)} chars")
        print(f"[DEBUG] User message length: {len(messages[1]['content'])} chars")
        print(f"[DEBUG] Ground truth answer provided: {ground_truth_answer}")

    # Apply the model's chat template
    inputs = tokenizer.apply_chat_template(
        messages,
        add_generation_prompt=True,
        tokenize=True,
        return_tensors="pt",
        return_dict=True,
        truncation=True,
        max_length=max_prompt_tokens,
    ).to(model.device)

    input_len = inputs["input_ids"].shape[-1]

    if debug:
        print(f"[DEBUG] Input tokens: {input_len}")

    try:
        with torch.no_grad():
            outputs = model.generate(
                **inputs,
                max_new_tokens=max_new_tokens,
                do_sample=False,
            )
    except torch.cuda.OutOfMemoryError:
        torch.cuda.empty_cache()
        return {"status": "error", "error": "cuda_oom_during_generate"}

    new_tokens = outputs[0, input_len:]
    raw = tokenizer.decode(new_tokens, skip_special_tokens=True).strip()

    if debug:
        print(f"[DEBUG] Generated {len(new_tokens)} new tokens")
        print(f"[DEBUG] Raw output preview: {raw[:500]}...")

    # JSON parse logic
    try:
        start = raw.find("{")
        end = raw.rfind("}")
        if start != -1 and end != -1 and end > start:
            raw_json = raw[start:end+1]
        else:
            raw_json = raw
        parsed = json.loads(raw_json)
        parsed["status"] = "success"
        return parsed
    except Exception as e:
        print(f"[ERROR] JSON parsing failed: {e}")
        return {"status": "parse_error", "raw": raw}


def cot_annotate_answer_verification_grok(example, ground_truth_answer, max_retries=3, debug=True):
    """
    MODIFIED: Generate reasoning that verifies a given answer using Grok API.
    """
    question = example["question"]
    history_text = build_history_text_answer_sessions(example, max_chars=50000, debug=debug)
    system = build_system_prompt_answer_verification(example)

    user_content = (
        f"CONVERSATION HISTORY:\n"
        f"{history_text}\n\n"
        f"QUESTION: {question}\n\n"
        f"CORRECT ANSWER: {ground_truth_answer}\n\n"
        "Your task: Verify this answer is correct by finding evidence and explaining the reasoning.\n"
        "If you cannot find evidence supporting this answer, set 'verified': false.\n\n"
        'Respond ONLY with valid JSON:\n'
        '{"evidence": "...", "reasoning": "...", "verified": true/false, "answer": "..."}\n\n'
        "JSON:"
    )

    messages = [
        {"role": "system", "content": system},
        {"role": "user", "content": user_content},
    ]

    if debug:
        print(f"[DEBUG] Ground truth answer provided: {ground_truth_answer}")
        print(f"[DEBUG] Total prompt length: {len(system) + len(user_content)} chars")

    for attempt in range(max_retries):
        try:
            response = grok_client.chat.completions.create(
                model=model_name,
                messages=messages,
                temperature=0.1,
                max_tokens=1024,
            )

            raw = response.choices[0].message.content.strip()

            if debug:
                print(f"[DEBUG] Grok response length: {len(raw)} chars")
                print(f"[DEBUG] Raw output preview: {raw[:500]}...")

            # Parse JSON
            start = raw.find("{")
            end = raw.rfind("}") + 1
            if start != -1 and end > start:
                parsed = json.loads(raw[start:end])
                parsed["status"] = "success"
                return parsed
            else:
                return {"status": "parse_error", "raw": raw}

        except Exception as e:
            error_str = str(e)
            print(f"[ERROR] Grok attempt {attempt + 1} failed: {error_str}")
            if attempt == max_retries - 1:
                return {"status": "error", "error": error_str}
            # Exponential backoff
            wait_time = 2 ** attempt
            print(f"[DEBUG] Waiting {wait_time}s before retry...")
            time.sleep(wait_time)

    return {"status": "error", "error": "max_retries_exceeded"}


def cot_annotate_answer_verification(example, ground_truth_answer, max_new_tokens=512, max_prompt_tokens=65536, debug=True):
    """
    Main annotation function for answer verification approach.
    Routes to local or Grok based on use_grok flag.
    """
    if use_grok == 1:
        return cot_annotate_answer_verification_grok(example, ground_truth_answer, debug=debug)
    else:
        return cot_annotate_answer_verification_local(example, ground_truth_answer, max_new_tokens, max_prompt_tokens, debug=debug)


# =============================================================================
# REASONING QUALITY VALIDATION
# =============================================================================

def validate_reasoning_quality(verification_result, ground_truth_answer, question, debug=True):
    """
    Validate that the reasoning actually supports the answer.

    Checks:
    1. Did the model find evidence?
    2. Does the reasoning logically connect evidence to answer?
    3. Did the model verify the answer as correct?

    Returns dict with 'is_valid', 'quality_score', and 'issues'
    """
    issues = []
    quality_score = 0

    if verification_result.get("status") != "success":
        return {
            "is_valid": False,
            "quality_score": 0,
            "issues": [f"Failed to get valid response: {verification_result.get('status')}"]
        }

    # Check 1: Evidence provided
    evidence = verification_result.get("evidence", "")
    if not evidence or len(evidence) < 10:
        issues.append("No meaningful evidence provided")
    else:
        quality_score += 25
        if debug:
            print(f"[VALIDATE] ✓ Evidence found ({len(evidence)} chars)")

    # Check 2: Reasoning provided
    reasoning = verification_result.get("reasoning", "")
    if not reasoning or len(reasoning) < 20:
        issues.append("No meaningful reasoning provided")
    else:
        quality_score += 25
        if debug:
            print(f"[VALIDATE] ✓ Reasoning provided ({len(reasoning)} chars)")

    # Check 3: Model verified the answer
    verified = verification_result.get("verified", False)
    if verified:
        quality_score += 25
        if debug:
            print(f"[VALIDATE] ✓ Model verified the answer as correct")
    else:
        issues.append("Model could not verify the answer - may indicate bad answer or insufficient context")
        if debug:
            print(f"[VALIDATE] ✗ Model did NOT verify the answer")

    # Check 4: Restated answer matches ground truth
    restated_answer = verification_result.get("answer", "")
    restated_answer = str(restated_answer)
    ground_truth_answer = str(ground_truth_answer)
    if restated_answer.strip().lower() == ground_truth_answer.strip().lower():
        quality_score += 25
        if debug:
            print(f"[VALIDATE] ✓ Restated answer matches ground truth")
    else:
        # Partial match is OK for longer answers
        if ground_truth_answer.lower() in restated_answer.lower() or restated_answer.lower() in ground_truth_answer.lower():
            quality_score += 15
            if debug:
                print(f"[VALIDATE] ~ Partial answer match")
        else:
            issues.append(f"Restated answer differs: '{restated_answer}' vs '{ground_truth_answer}'")
            if debug:
                print(f"[VALIDATE] ✗ Answer mismatch: '{restated_answer[:50]}...' vs '{ground_truth_answer[:50]}...'")

    is_valid = quality_score >= 50 and verified

    if debug:
        print(f"[VALIDATE] Final score: {quality_score}/100, Valid: {is_valid}")
        if issues:
            print(f"[VALIDATE] Issues: {issues}")

    return {
        "is_valid": is_valid,
        "quality_score": quality_score,
        "issues": issues
    }


# =============================================================================
# LEGACY FUNCTIONS (kept for backwards compatibility)
# =============================================================================

def build_system_prompt(example):
    """Original system prompt builder - kept for reference."""
    qt = example["question_type"]

    h_types = ['single-session-preference', 'single-session-answer', ]

    if qt not in h_types:
      print(f"[DEBUG] Question type: {qt}")

    if qt == "temporal-reasoning":
        base = (
            "detailed thinking on\n\n"
            "You are an assistant that specializes in temporal reasoning over a chat transcript.\n"
            "You will be given conversation history and a question about the ORDER of events\n"
            "(for example: which event happened first, which came later, or which one I did first).\n\n"
            "Your goal is to infer the most likely ordering of the events based on the user's words.\n"
            "You do NOT need exact timestamps. It is fine to reason using:\n"
            "- relative phrases like 'three weeks ago', 'last month', 'yesterday', 'earlier today',\n"
            "  'recently', 'then', 'after that', etc.\n"
            "- the narrative order in which the user describes events (e.g. 'first I X, then I Y').\n"
            "- the question date if it is provided.\n\n"
            "Reasoning steps:\n"
            "1. Identify the events that the question is asking you to compare.\n"
            "2. Collect all timing clues for those events from the conversation.\n"
            "3. Use those clues to build a simple relative timeline (which seems earlier / later).\n"
            "4. Choose the SINGLE best-supported event as the answer.\n"
            "   - When the question lists options (e.g. 'A or B?'), your final answer should repeat\n"
            "     exactly one of those option texts.\n"
            "5. Only answer 'cannot be determined' if there is genuinely no information at all about\n"
            "   the relative order OR the information is directly contradictory.\n"
            "   Lack of precise dates or times by itself is NOT a reason to say 'cannot be determined'.\n\n"
            "Return JSON with keys 'reasoning' and 'answer', where 'reasoning' shows your timeline\n"
            "and 'answer' is a short sentence that directly answers the temporal question."
        )
        return "detailed thinking on\n\n" + base

    elif qt == "single-session-preference":
        return (
            "detailed thinking on\n\n"
            "You are a preference-mining assistant.\n"
            "Read the conversation between user and assistant.\n\n"
            "Your task is NOT to answer the user's question directly.\n"
            "Instead, infer what kind of answer the user would PREFER to receive "
            "for similar questions in the future.\n\n"
            "Describe their preferences in 1–3 sentences, focusing on:\n"
            "- which tools / products / topics they care about,\n"
            "- what level of detail or depth they want,\n"
            "- what they seem NOT to want (things they ignore or push back on).\n\n"
            "Return JSON with keys 'reasoning' and 'answer', where 'answer' is "
            "the preference summary.\n"
            "Use only information from the conversation; do not invent facts."
        )

    elif qt == "single-session-answer":
        return (
            "detailed thinking on\n\n"
            "You are a careful reasoning assistant.\n"
            "Read the conversation and answer the user's question as accurately as possible.\n"
            "Think step by step, then give a concise final answer.\n"
            "Return JSON with keys 'reasoning' and 'answer'."
        )

    else:
        # safe fallback
        return (
            "detailed thinking on\n\n"
            "You are a careful reasoning assistant.\n"
            "Read the conversation and answer the user's question.\n"
            "Return JSON with keys 'reasoning' and 'answer'."
        )


def make_model_input(example):
    return {
        "question": example["question"],
        "question_date": example["question_date"],
        "haystack_dates": example["haystack_dates"],
        "haystack_session_ids": example["haystack_session_ids"],
        "answer_session_ids": example["answer_session_ids"],
        "haystack_session_ids": example["haystack_session_ids"],
        "question_type": example["question_type"],
        "haystack_sessions": [
            [
                {
                    "role": turn["role"],
                    "content": turn["content"],
                    "has_answer": turn["has_answer"]
                }
                for turn in session
            ]
            for session in example["haystack_sessions"]
        ],
    }


def get_label(example):
    return {
        "id": example["question_id"],
        "answer": example["answer"],
    }

def save_example(example, out_dir="."):
    # Number of sessions
    num_sessions = len(example["haystack_sessions"])

    # Get question_id and make sure it's filename-safe
    qid = example["question_id"]

    # Build filename like "3_gpt4_2655b836.json"
    filename = f"{num_sessions}_{qid}.json"
    path = os.path.join(out_dir, filename)

    # Save to disk
    with open(path, "w", encoding="utf-8") as f:
        json.dump(example, f, ensure_ascii=False, indent=2)

    return path


# Default Approach

In [8]:
import os
from transformers import pipeline, BitsAndBytesConfig, set_seed
from transformers import AutoTokenizer, AutoModelForCausalLM
import torch
from google.colab import userdata
import time

# =============================================================================
# MODEL SELECTION FLAG
# =============================================================================
# use_grok = 0  -> Use local model (default)
# use_grok = 1  -> Use xAI Grok API (OpenAI-compatible) via https://api.x.ai/v1
# =============================================================================
use_grok = 1

# Setup based on flag
if use_grok == 0:
    # --- LOCAL MODEL SETUP ---
    os.environ['HF_CACHE'] = '/content/drive/My Drive/transformers_cache'
    hf_token = userdata.get('HF_TOKEN')
    os.environ['HF_TOKEN'] = hf_token or ''

    set_seed(1234)

    local_model_flag = 0
    if local_model_flag == 0:
        model_name = "nvidia/Llama-3.1-Nemotron-Nano-8B-v1"
    elif local_model_flag == 1:
        model_name = "google/gemma-2-9b-it"

    bnb_cfg = BitsAndBytesConfig(
        load_in_4bit=True,
        bnb_4bit_compute_dtype=torch.bfloat16,
        bnb_4bit_use_double_quant=True,
        bnb_4bit_quant_type="nf4",
    )

    tokenizer = AutoTokenizer.from_pretrained(model_name)

    model = AutoModelForCausalLM.from_pretrained(
        model_name,
        quantization_config=bnb_cfg,
        device_map="auto",
    )
    model.eval()

    print(f"Loaded local model: {model_name}")
    print(f"Device: {model.device}, Dtype: {next(model.parameters()).dtype}")

    grok_client = None  # Not used

else:
    # --- xAI GROK API SETUP (OpenAI-compatible) ---
    # Docs: https://docs.x.ai
    from openai import OpenAI

    xai_api_key = userdata.get("groq_key")

    grok_client = OpenAI(api_key=xai_api_key, base_url="https://api.x.ai/v1")

    # Pick a Grok model. Change this if you want a different tier (e.g., grok-4-fast-reasoning).
    model_name = "grok-4-1-fast-reasoning"#"grok-4"

    # Set placeholders for local model vars (not used)
    model = None
    tokenizer = None

    print(f"Using xAI Grok API with model: {model_name}")


Using xAI Grok API with model: grok-4-1-fast-reasoning


In [15]:
import os
import json
import torch

out_dir = "lme_jsons_verified"
reset = False

# =============================================================================
# CONFIGURATION FLAGS
# =============================================================================
DEBUG_MODE = True           # Enable verbose debugging output
save_failed_to_file = True  # Save failed IDs to a file for persistence across sessions

# =============================================================================
# TRACKING SETS
# =============================================================================
# 1) Build a set of already-processed question_ids from existing files
processed_ids = set()

# 2) Runtime set of failed question_ids (verification didn't pass)
failed_ids = set()

# 3) Load previously failed IDs from file (if exists) to avoid retrying
failed_ids_file = os.path.join(out_dir, "_failed_ids.json")

if os.path.isdir(out_dir):
    if reset:
        for filename in os.listdir(out_dir):
            file_path = os.path.join(out_dir, filename)
            if os.path.isfile(file_path):
                os.remove(file_path)
                print(f'{filename} removed')
        failed_ids = set()  # Clear failed IDs on reset
    else:
        # Load processed IDs from saved JSON files
        for fname in os.listdir(out_dir):
            if not fname.endswith(".json"):
                continue
            if fname.startswith("_"):  # Skip meta files like _failed_ids.json
                continue
            base = os.path.splitext(fname)[0]
            parts = base.split("_", 1)
            if len(parts) != 2:
                continue
            _, qid = parts
            processed_ids.add(qid)

        # Load previously failed IDs
        if os.path.exists(failed_ids_file):
            with open(failed_ids_file, "r") as f:
                failed_ids = set(json.load(f))
            print(f"Loaded {len(failed_ids)} previously failed IDs from file")
else:
    os.makedirs(out_dir, exist_ok=True)

print(f"Found {len(processed_ids)} existing successful test files")
print(f"Found {len(failed_ids)} previously failed test IDs")

# =============================================================================
# HELPER FUNCTION TO SAVE FAILED IDS
# =============================================================================
def save_failed_ids():
    """Persist failed IDs to file for next session."""
    if save_failed_to_file:
        with open(failed_ids_file, "w") as f:
            json.dump(list(failed_ids), f, indent=2)
        print(f"[SAVE] Saved {len(failed_ids)} failed IDs to {failed_ids_file}")

# =============================================================================
# MAIN PROCESSING LOOP - ANSWER VERIFICATION APPROACH
# =============================================================================
# Statistics tracking
stats = {
    "processed": 0,
    "skipped_already_done": 0,
    "skipped_previously_failed": 0,
    "skipped_too_many_sessions": 0,
    "verification_passed": 0,
    "verification_failed": 0,
    "errors": 0,
    "low_quality": 0,
}

print("\n" + "="*60)
print("STARTING ANSWER VERIFICATION PROCESSING")
print("="*60)
print("Approach: Give LLM the correct answer, ask it to verify with reasoning")
print("="*60 + "\n")

try:
    for i, test in enumerate(LME):
        qid = test["question_id"]

        # Skip if already successfully processed
        if qid in processed_ids:
            stats["skipped_already_done"] += 1
            continue

        # Skip if previously failed verification
        if qid in failed_ids:
            if DEBUG_MODE:
                print(f"[SKIP-FAILED] Question ID {qid} previously failed, skipping.")
            stats["skipped_previously_failed"] += 1
            continue

        # # Skip if too many sessions
        # if len(test['haystack_dates']) > 4:
        #     stats["skipped_too_many_sessions"] += 1
        #     continue

        trimmed_example = make_model_input(test)
        ground_truth = test["answer"]

        print(f"\n{'='*60}")
        print(f"[{stats['processed']+1}] Question ID: {qid}")
        print(f"{'='*60}")
        print(f"Question Type: {test['question_type']}")
        print(f"Sessions: {len(test['haystack_dates'])}")
        print(f"Question: {test['question']}")
        print(f"Ground Truth Answer: {ground_truth}")
        print("-"*60)

        # =================================================================
        # ANSWER VERIFICATION STEP
        # =================================================================
        print(f"\n[STEP 1] Asking LLM to verify the answer with reasoning...")

        verification_result = cot_annotate_answer_verification(
            trimmed_example,
            ground_truth,
            debug=DEBUG_MODE
        )

        print(f"\n[STEP 2] Verification result:")
        print(json.dumps(verification_result, indent=2)[:1500])
        if len(json.dumps(verification_result)) > 1500:
            print("... [truncated]")

        stats["processed"] += 1

        # Check for errors
        if verification_result.get("status") == "error":
            print(f"[ERROR] {verification_result.get('error')}")
            stats["errors"] += 1
            failed_ids.add(qid)
            continue

        if verification_result.get("status") == "parse_error":
            print(f"[ERROR] Failed to parse JSON response")
            stats["errors"] += 1
            failed_ids.add(qid)
            continue

        # =================================================================
        # QUALITY VALIDATION STEP
        # =================================================================
        print(f"\n[STEP 3] Validating reasoning quality...")

        quality_result = validate_reasoning_quality(
            verification_result,
            ground_truth,
            test["question"],
            debug=DEBUG_MODE
        )

        if not quality_result["is_valid"]:
            print(f"[QUALITY FAILED] Score: {quality_result['quality_score']}/100")
            print(f"[QUALITY FAILED] Issues: {quality_result['issues']}")

            # Check if the model couldn't verify the answer
            if not verification_result.get("verified", False):
                print(f"[WARNING] Model could not verify this answer - ground truth may be incorrect!")
                stats["verification_failed"] += 1
            else:
                stats["low_quality"] += 1

            failed_ids.add(qid)
            continue

        print(f"[QUALITY PASSED] Score: {quality_result['quality_score']}/100")
        stats["verification_passed"] += 1

        # =================================================================
        # SAVE SUCCESSFUL RESPONSE
        # =================================================================
        if "model_annotations" not in test:
            test["model_annotations"] = {}

        test["model_annotations"][model_name] = {
            "status": "ok",
            "approach": "answer_verification",
            "evidence": verification_result.get("evidence"),
            "reasoning": verification_result.get("reasoning"),
            "verified": verification_result.get("verified"),
            "answer": verification_result.get("answer"),
            "quality_score": quality_result["quality_score"],
        }

        save_example(test, out_dir=out_dir)
        processed_ids.add(qid)
        print(f"[SAVED] {qid}")

        # Periodic cleanup
        if stats["processed"] % 20 == 0:
            if use_grok == 0:  # Only for local model
                torch.cuda.empty_cache()
            save_failed_ids()  # Periodic save of failed IDs

        # # Optional: break after N examples for testing
        # if stats["processed"] >= 50:
        #     print("\n[STOPPING] Reached 50 processed examples")
        #     break

except KeyboardInterrupt:
    print("\n[INTERRUPTED] Saving failed IDs before exit...")

finally:
    # Always save failed IDs at the end
    save_failed_ids()

    # Print final statistics
    print("\n" + "="*60)
    print("FINAL STATISTICS")
    print("="*60)
    for key, value in stats.items():
        print(f"  {key}: {value}")
    print(f"  total_failed_ids: {len(failed_ids)}")
    print(f"  total_processed_ids: {len(processed_ids)}")

    # Calculate success rate
    if stats["processed"] > 0:
        success_rate = stats["verification_passed"] / stats["processed"] * 100
        print(f"\n  SUCCESS RATE: {success_rate:.1f}%")


Loaded 99 previously failed IDs from file
Found 401 existing successful test files
Found 99 previously failed test IDs

STARTING ANSWER VERIFICATION PROCESSING
Approach: Give LLM the correct answer, ask it to verify with reasoning

[SKIP-FAILED] Question ID gpt4_8c8961ae previously failed, skipping.
[SKIP-FAILED] Question ID gpt4_fe651585 previously failed, skipping.
[SKIP-FAILED] Question ID 46a3abf7 previously failed, skipping.
[SKIP-FAILED] Question ID gpt4_2f8be40d previously failed, skipping.
[SKIP-FAILED] Question ID gpt4_194be4b3 previously failed, skipping.
[SKIP-FAILED] Question ID d851d5ba previously failed, skipping.
[SKIP-FAILED] Question ID edced276_abs previously failed, skipping.
[SKIP-FAILED] Question ID gpt4_372c3eed_abs previously failed, skipping.
[SKIP-FAILED] Question ID 2133c1b5 previously failed, skipping.
[SKIP-FAILED] Question ID 50635ada previously failed, skipping.
[SKIP-FAILED] Question ID a2f3aa27 previously failed, skipping.
[SKIP-FAILED] Question ID dad22

Current issue is that despite having the model prompting to get the user preferences, the model is not sophisticated enough to pull actual preferences... while a similar prompt for something like GPT 5 would give you something closer to the answer label

In [14]:
%%capture
!zip -r lme_jsons_verified.zip lme_jsons_verified


# Distillation with Grok

In [ ]:
import os
import json
import time
import google.generativeai as genai
from google.colab import userdata
from openai import OpenAI

# --- xAI GROK API SETUP (OpenAI-compatible) ---
xai_api_key = (
    userdata.get("XAI_API_KEY")
    or userdata.get("xai_api_key")
    or userdata.get("xai_key")
    or os.getenv("XAI_API_KEY")
)
if not xai_api_key:
    raise ValueError(
        "Missing xAI API key. In Colab: add a secret named XAI_API_KEY (or xai_api_key)."
    )

grok_client = OpenAI(api_key=xai_api_key, base_url="https://api.x.ai/v1")

# Teacher model for rationale generation (adjust as desired)
grok_model = "grok-4"

# --- Optional Gemini fallback ---
# If you want Gemini fallback, add a Colab secret named GEMINI_API_KEY.
try:
    gemini_key = userdata.get("GEMINI_API_KEY") or os.getenv("GEMINI_API_KEY")
    if gemini_key:
        genai.configure(api_key=gemini_key)
        gemini_model = genai.GenerativeModel("gemini-1.5-flash")
    else:
        gemini_model = None
except Exception:
    gemini_model = None


In [ ]:
def generate_rationale_grok(history_text, question, ground_truth_answer, max_retries=3):
    """Generate reasoning trace using xAI Grok via the xAI API."""

    prompt = f"""You are helping build a training dataset for a reasoning model.

Given a conversation history and a question, generate a detailed step-by-step reasoning trace
that shows HOW to find the answer. The reasoning should:
1. Identify what information is needed to answer the question
2. Locate the specific session(s) and turn(s) containing relevant information
3. Extract and synthesize the key facts
4. Arrive at the final answer

CONVERSATION HISTORY:
{history_text}

QUESTION: {question}

GROUND TRUTH ANSWER: {ground_truth_answer}

Generate a reasoning trace that would lead to this answer. Be specific about which
parts of the conversation contain the relevant information.

Respond in this exact JSON format:
{{
    "reasoning": "Step 1: [identify what we need to find]\\nStep 2: [locate relevant information in Session X, Turn Y]\\nStep 3: [extract key facts]\\nStep 4: [synthesize to get answer]",
    "answer": "[final answer matching ground truth]"
}}

JSON:"""

    for attempt in range(max_retries):
        try:
            response = grok_client.chat.completions.create(
                model=grok_model,  # e.g., "grok-4"
                messages=[{"role": "user", "content": prompt}],
                temperature=0.1,
                max_tokens=1024,
            )

            raw = response.choices[0].message.content.strip()

            # Parse JSON
            start = raw.find("{")
            end = raw.rfind("}") + 1
            if start != -1 and end > start:
                parsed = json.loads(raw[start:end])
                return {"status": "success", **parsed}
            else:
                return {"status": "parse_error", "raw": raw}

        except Exception as e:
            if attempt == max_retries - 1:
                return {"status": "error", "error": str(e)}
            time.sleep(2 ** attempt)  # Exponential backoff

    return {"status": "max_retries_exceeded"}


def generate_rationale_gemini(history_text, question, ground_truth_answer):
    """Fallback/alternative using Gemini 1.5 Flash (free)."""

    prompt = f"""You are helping build a training dataset. Given conversation history and a question,
generate a step-by-step reasoning trace showing how to find the answer.

CONVERSATION HISTORY:
{history_text}

QUESTION: {question}
GROUND TRUTH ANSWER: {ground_truth_answer}

Generate detailed reasoning that identifies which session/turn contains the answer.

Respond as JSON: {{"reasoning": "...", "answer": "..."}}"""

    try:
        if gemini_model is None:
            return {"status": "error", "error": "Gemini fallback requested but GEMINI_API_KEY/gemini_model is not configured."}
        response = gemini_model.generate_content(prompt)
        raw = response.text.strip()

        start = raw.find("{")
        end = raw.rfind("}") + 1
        if start != -1 and end > start:
            parsed = json.loads(raw[start:end])
            return {"status": "success", **parsed}
        return {"status": "parse_error", "raw": raw}

    except Exception as e:
        return {"status": "error", "error": str(e)}


In [ ]:
import json
import time
from tqdm import tqdm

def build_reasoning_dataset(lme_examples, output_dir="reasoning_dataset", use_grok=True):
    """
    Build dataset where each example has:
    - input (conversation + question)
    - reasoning trace (from teacher model)
    - answer
    """

    os.makedirs(output_dir, exist_ok=True)

    results = []

    for i, example in enumerate(tqdm(lme_examples)):
        qid = example["question_id"]
        question = example["question"]
        ground_truth = example["answer"]
        question_type = example["question_type"]

        # Build history text (using your existing function)
        history_text = build_history_text_answer_sessions(example, max_chars=30000)

        # Generate rationale from teacher model
        if use_grok:
            teacher_output = generate_rationale_grok(
                history_text, question, ground_truth
            )
        else:
            teacher_output = generate_rationale_gemini(
                history_text, question, ground_truth
            )

        # Build the dataset entry
        entry = {
            "question_id": qid,
            "question_type": question_type,
            "question": question,
            "ground_truth_answer": ground_truth,
            "conversation_history": history_text,
            "teacher_model": grok_model if use_grok else "gemini-1.5-flash",
            "teacher_output": teacher_output,
        }

        # If successful, also create the "ideal" training format
        if teacher_output.get("status") == "success":
            entry["training_input"] = (
                f"Conversation history:\n{history_text}\n\n"
                f"Question: {question}\n\n"
                f"Think step by step, then provide your answer as JSON with "
                f"'reasoning' and 'answer' keys."
            )
            entry["training_output"] = json.dumps({
                "reasoning": teacher_output["reasoning"],
                "answer": teacher_output["answer"]
            }, indent=2)

        results.append(entry)

        # Save incrementally
        output_path = os.path.join(output_dir, f"{qid}.json")
        with open(output_path, "w") as f:
            json.dump(entry, f, indent=2)

        # Rate limiting for free tiers
        time.sleep(0.5)  # Grok is fast, but be respectful

        # Progress update
        if (i + 1) % 10 == 0:
            success_count = sum(1 for r in results if r["teacher_output"].get("status") == "success")
            print(f"Processed {i+1}, Success rate: {success_count}/{len(results)}")

    # Save full dataset
    with open(os.path.join(output_dir, "full_dataset.json"), "w") as f:
        json.dump(results, f, indent=2)

    return results


In [ ]:
examples_to_process = [ex for ex in LME if len(ex['haystack_dates']) <= 4]

# Playground
examples_to_process[0:5]

print(f"Processing {len(examples_to_process)} examples...")
dataset = build_reasoning_dataset(examples_to_process[0:5], use_grok=True)


In [ ]:
dataset
